In [1]:
import json
from datetime import datetime, timedelta
import pandas as pd
from tqdm import tqdm

from utils import get_time, get_coords, validate_datetime_format, validate_time_format, is_at_stop, BUS_DATA_MEASUREMENT_TIME

In [2]:
filepath_morning = "../data/bus-locations-2024-02-19 09:35:12.222315.json"
filepath_evening = "../data/bus-locations-2024-02-18 20:29:31.691732.json"

timestamp_morning = datetime.strptime("2024-02-19 09:35:12", '%Y-%m-%d %H:%M:%S')
timestamp_evening = datetime.strptime("2024-02-18 20:29:31", '%Y-%m-%d %H:%M:%S')
download_time = timestamp_morning

In [3]:
with open(filepath_morning, "r", encoding="utf-8") as json_file:
    buses_data = json.load(json_file)

buses_data

[{'Lines': '219',
  'Lon': 21.1025511,
  'VehicleNumber': '1000',
  'Time': '2024-02-19 09:35:03',
  'Lat': 52.2227915,
  'Brigade': '1'},
 {'Lines': '219',
  'Lon': 21.1443788,
  'VehicleNumber': '1001',
  'Time': '2024-02-19 09:34:56',
  'Lat': 52.1864221,
  'Brigade': '3'},
 {'Lines': '213',
  'Lon': 21.116943,
  'VehicleNumber': '1002',
  'Time': '2024-02-19 02:57:59',
  'Lat': 52.234666,
  'Brigade': '1'},
 {'Lines': '219',
  'Lon': 21.1703736,
  'VehicleNumber': '1003',
  'Time': '2024-02-19 09:35:01',
  'Lat': 52.1961883,
  'Brigade': '2'},
 {'Lines': '213',
  'Lon': 21.220208,
  'VehicleNumber': '1004',
  'Time': '2024-02-19 09:34:57',
  'Lat': 52.157376,
  'Brigade': '3'},
 {'Lines': '213',
  'Lon': 21.2088148,
  'VehicleNumber': '1005',
  'Time': '2024-02-19 09:34:54',
  'Lat': 52.1605016,
  'Brigade': '4'},
 {'Lines': '119',
  'Lon': 21.114108,
  'VehicleNumber': '1006',
  'Time': '2024-02-19 07:03:08',
  'Lat': 52.234278,
  'Brigade': '3'},
 {'Lines': '213',
  'Lon': 21.102

In [4]:
filepath_schedules = "../data/bus-schedules.json"

with open(filepath_schedules, "r", encoding="utf-8") as json_file:
        schedules_data = json.load(json_file)
    
schedules_data

{'1001,01,102': ['05:06:00',
  '05:34:00',
  '05:49:00',
  '06:05:00',
  '06:20:00',
  '06:37:00',
  '06:53:00',
  '07:08:00',
  '07:23:00',
  '07:38:00',
  '07:53:00',
  '08:08:00',
  '08:23:00',
  '08:38:00',
  '08:53:00',
  '09:08:00',
  '09:25:00',
  '09:45:00',
  '10:05:00',
  '10:25:00',
  '10:45:00',
  '11:05:00',
  '11:25:00',
  '11:45:00',
  '12:05:00',
  '12:25:00',
  '12:45:00',
  '13:05:00',
  '13:25:00',
  '13:45:00',
  '14:05:00',
  '14:22:00',
  '14:37:00',
  '14:52:00',
  '15:08:00',
  '15:23:00',
  '15:38:00',
  '15:53:00',
  '16:08:00',
  '16:23:00',
  '16:38:00',
  '16:53:00',
  '17:08:00',
  '17:23:00',
  '17:38:00',
  '17:53:00',
  '18:07:00',
  '18:22:00',
  '18:37:00',
  '18:52:00',
  '19:10:00',
  '19:30:00',
  '19:50:00',
  '20:10:00',
  '20:30:00',
  '20:50:00',
  '21:09:00',
  '21:29:00',
  '21:49:00',
  '22:09:00',
  '22:36:00',
  '23:06:00',
  '23:36:00',
  '24:06:00'],
 '1001,01,123': ['04:56:00',
  '05:26:00',
  '05:52:00',
  '06:08:00',
  '06:24:00',
  '

In [5]:
filepath_bus_stops = "../data/bus-stops.json"

with open(filepath_bus_stops, "r", encoding="utf-8") as json_file:
    bus_stops_data = json.load(json_file)

bus_stops_data

{'result': [{'values': [{'value': '1001', 'key': 'zespol'},
    {'value': '01', 'key': 'slupek'},
    {'value': 'Kijowska', 'key': 'nazwa_zespolu'},
    {'value': '2201', 'key': 'id_ulicy'},
    {'value': '52.248455', 'key': 'szer_geo'},
    {'value': '21.044827', 'key': 'dlug_geo'},
    {'value': 'al.Zieleniecka', 'key': 'kierunek'},
    {'value': '2023-10-14 00:00:00.0', 'key': 'obowiazuje_od'}]},
  {'values': [{'value': '1001', 'key': 'zespol'},
    {'value': '02', 'key': 'slupek'},
    {'value': 'Kijowska', 'key': 'nazwa_zespolu'},
    {'value': '2201', 'key': 'id_ulicy'},
    {'value': '52.249078', 'key': 'szer_geo'},
    {'value': '21.044443', 'key': 'dlug_geo'},
    {'value': 'Ząbkowska', 'key': 'kierunek'},
    {'value': '2023-10-14 00:00:00.0', 'key': 'obowiazuje_od'}]},
  {'values': [{'value': '1001', 'key': 'zespol'},
    {'value': '03', 'key': 'slupek'},
    {'value': 'Kijowska', 'key': 'nazwa_zespolu'},
    {'value': '2201', 'key': 'id_ulicy'},
    {'value': '52.248928', '

In [6]:
bus_stops_to_locations = {(bus_stop["values"][0]["value"], bus_stop["values"][1]["value"]): (bus_stop["values"][4]["value"], bus_stop["values"][5]["value"]) for bus_stop in bus_stops_data["result"]}

bus_stops_to_locations

{('1001', '01'): ('52.248455', '21.044827'),
 ('1001', '02'): ('52.249078', '21.044443'),
 ('1001', '03'): ('52.248928', '21.044169'),
 ('1001', '04'): ('52.249969', '21.041588'),
 ('1001', '05'): ('52.250319', '21.043861'),
 ('1001', '06'): ('52.250078', '21.043848'),
 ('1001', '07'): ('52.250228', '21.043690'),
 ('1001', '08'): ('52.249944', '21.044087'),
 ('1001', '88'): ('52.249944', '21.044087'),
 ('1002', '01'): ('52.251325', '21.038457'),
 ('1002', '02'): ('52.251790', '21.038592'),
 ('1002', '03'): ('52.251583', '21.038448'),
 ('1002', '04'): ('52.251944', '21.037888'),
 ('1002', '06'): ('52.253108', '21.036732'),
 ('1003', '01'): ('52.253739', '21.035454'),
 ('1003', '02'): ('52.255298', '21.034611'),
 ('1003', '03'): ('52.254118', '21.033248'),
 ('1003', '04'): ('52.255099', '21.036174'),
 ('1003', '05'): ('52.254287', '21.033324'),
 ('1003', '06'): ('52.256048', '21.038309'),
 ('1003', '07'): ('52.253857', '21.035613'),
 ('1003', '08'): ('52.255370', '21.034193'),
 ('1003', 

In [7]:
buses = [bus["VehicleNumber"] for bus in buses_data if isinstance(bus, dict) and "VehicleNumber" in bus]
bus_lines = [bus["Lines"] for bus in buses_data if isinstance(bus, dict) and "Lines" in bus]

print(f"skipped {len(buses_data) - len(buses)} elements out of {len(buses_data)}")

buses

skipped 444 elements out of 85341


['1000',
 '1001',
 '1002',
 '1003',
 '1004',
 '1005',
 '1006',
 '1007',
 '10071',
 '10072',
 '10073',
 '10074',
 '10075',
 '1008',
 '1009',
 '1010',
 '1011',
 '1012',
 '1013',
 '1014',
 '1020',
 '1021',
 '1022',
 '1023',
 '1024',
 '1025',
 '1026',
 '1027',
 '1028',
 '1029',
 '1030',
 '1031',
 '1032',
 '1033',
 '1034',
 '1035',
 '1036',
 '1037',
 '1038',
 '1039',
 '1040',
 '1041',
 '1042',
 '1043',
 '1044',
 '1045',
 '1046',
 '1048',
 '1049',
 '1050',
 '1051',
 '1052',
 '1053',
 '1054',
 '1055',
 '1056',
 '1057',
 '1058',
 '1059',
 '1060',
 '1061',
 '1062',
 '1063',
 '1064',
 '1065',
 '1066',
 '1067',
 '1068',
 '1069',
 '1070',
 '1071',
 '1072',
 '1073',
 '1074',
 '1075',
 '1076',
 '1077',
 '1078',
 '1079',
 '1101',
 '1102',
 '1106',
 '1109',
 '1110',
 '1112',
 '1115',
 '1117',
 '1118',
 '1119',
 '11201',
 '11202',
 '1200',
 '1201',
 '1202',
 '1203',
 '1204',
 '1205',
 '1206',
 '1207',
 '1208',
 '1209',
 '1211',
 '1212',
 '1213',
 '1214',
 '1216',
 '1217',
 '1218',
 '1219',
 '1220',
 '1

In [8]:
bus_lines = list(set(bus_lines))
bus_lines

['158',
 '221',
 '178',
 'L-8',
 '146',
 '709',
 '145',
 'N46',
 '175',
 '222',
 '735',
 'N34',
 '160',
 '134',
 '225',
 '110',
 '197',
 '523',
 '208',
 '525',
 '174',
 'L16',
 '256',
 '104',
 '727',
 '128',
 '517',
 '116',
 '251',
 '262',
 '192',
 'L50',
 '245',
 '520',
 'L29',
 '414',
 'L46',
 '731',
 '212',
 '320',
 '108',
 '713',
 '332',
 'L14',
 '149',
 '193',
 '217',
 '132',
 '182',
 '720',
 '228',
 '141',
 'L40',
 '503',
 'L45',
 '704',
 '198',
 '239',
 '702',
 '165',
 '518',
 '139',
 '105',
 '166',
 '850',
 'L49',
 '815',
 '157',
 '199',
 '102',
 'N03',
 '147',
 'L-7',
 '331',
 '522',
 '163',
 '716',
 '186',
 '249',
 '121',
 '210',
 '196',
 '171',
 'L28',
 '106',
 '184',
 '143',
 'L-6',
 '728',
 '516',
 'L35',
 '140',
 '154',
 'ZA1',
 '500',
 '724',
 'L-2',
 'L36',
 '126',
 '512',
 '203',
 '159',
 '114',
 '339',
 '170',
 'E-1',
 'L22',
 '739',
 '721',
 '123',
 '152',
 '999',
 '743',
 'L48',
 'L20',
 '172',
 '183',
 '738',
 'L51',
 '148',
 '133',
 '218',
 '180',
 '714',
 '127',


In [9]:
bus_locations = {bus_line: [] for bus_line in bus_lines}

for data_point in buses_data:
    if not isinstance(data_point, dict) or not validate_datetime_format(get_time(data_point)):
        continue
    time = datetime.strptime(data_point['Time'], '%Y-%m-%d %H:%M:%S')
    if time < download_time:
        continue
    bus_locations[data_point["Lines"]].append((time, (get_coords(data_point))))

for bus_line in bus_locations:
    bus_locations[bus_line] = sorted(bus_locations[bus_line], key=lambda x: x[0])


bus_locations

{'158': [(datetime.datetime(2024, 2, 19, 9, 36, 55), (52.2195717, 20.97092)),
  (datetime.datetime(2024, 2, 19, 9, 37), (52.231377, 21.018099)),
  (datetime.datetime(2024, 2, 19, 9, 37), (52.236736, 21.110271)),
  (datetime.datetime(2024, 2, 19, 9, 37, 1), (52.2116354, 20.949312)),
  (datetime.datetime(2024, 2, 19, 9, 37, 1), (52.236328, 21.08779)),
  (datetime.datetime(2024, 2, 19, 9, 37, 2), (52.222332, 20.979528)),
  (datetime.datetime(2024, 2, 19, 9, 37, 2), (52.232212, 21.023512)),
  (datetime.datetime(2024, 2, 19, 9, 37, 4), (52.196224, 20.9265)),
  (datetime.datetime(2024, 2, 19, 9, 37, 4), (52.236289, 21.1126965)),
  (datetime.datetime(2024, 2, 19, 9, 37, 4), (52.2398036, 21.0600942)),
  (datetime.datetime(2024, 2, 19, 9, 37, 58), (52.2199617, 20.9719183)),
  (datetime.datetime(2024, 2, 19, 9, 38, 7), (52.232307, 21.023726)),
  (datetime.datetime(2024, 2, 19, 9, 38, 9), (52.221325, 20.975468)),
  (datetime.datetime(2024, 2, 19, 9, 38, 9), (52.211632, 20.949324)),
  (datetime.da

In [10]:
from utils import calculate_distance

In [18]:
delayed_buses = []
bus_lines_not_found = []
not_arrived = 0
on_time = 0

for id in tqdm(schedules_data):
    bus_stop_id, bus_stop_nr, bus_line = id.split(',')

    times = schedules_data[id]
    times = [datetime.strptime(time, '%H:%M:%S').time()
             for time in times if validate_time_format(time)]
    times = [download_time.replace(
        hour=t.hour, minute=t.minute, second=t.second) for t in times]
    times = [time for time in times if download_time <=
             time <= download_time + BUS_DATA_MEASUREMENT_TIME]

    bus_stop_loc = bus_stops_to_locations[(bus_stop_id, bus_stop_nr)]

    try:
        locations = bus_locations[bus_line]
    except KeyError as e:
        bus_lines_not_found.append(bus_line)
        continue

    for time in times:
        arrival = next(((t, bus_loc) for (t, bus_loc) in locations if t >= time -
                       timedelta(minutes=2) and is_at_stop(bus_loc, bus_stop_loc)), None)

        distances = [(t, calculate_distance(bus_loc, bus_stop_loc), is_at_stop(
            bus_loc, bus_stop_loc)) for (t, bus_loc) in locations]

        if arrival is None:
            not_arrived += 1
            continue

        delay = arrival[0] - time
        if delay >= timedelta(minutes=2):
            delayed_buses.append((bus_line, bus_stop_id, time, delay))
        else:
            on_time += 1

print(len(set(bus_lines_not_found)), not_arrived)

print(f"number of delayed buses: {len(delayed_buses)}, number of buses on time: {on_time}")
delayed_buses


100%|██████████| 20851/20851 [01:49<00:00, 191.20it/s] 


77 2536
number of delayed buses: 7906, number of buses on time: 21859


[('147',
  '1001',
  datetime.datetime(2024, 2, 19, 10, 27),
  datetime.timedelta(seconds=247)),
 ('166',
  '1001',
  datetime.datetime(2024, 2, 19, 9, 54),
  datetime.timedelta(seconds=266)),
 ('509',
  '1001',
  datetime.datetime(2024, 2, 19, 10, 3),
  datetime.timedelta(seconds=159)),
 ('138',
  '1001',
  datetime.datetime(2024, 2, 19, 9, 44),
  datetime.timedelta(seconds=312)),
 ('166',
  '1001',
  datetime.datetime(2024, 2, 19, 10, 4),
  datetime.timedelta(seconds=288)),
 ('166',
  '1001',
  datetime.datetime(2024, 2, 19, 10, 24),
  datetime.timedelta(seconds=420)),
 ('509',
  '1001',
  datetime.datetime(2024, 2, 19, 10, 27),
  datetime.timedelta(seconds=247)),
 ('512',
  '1001',
  datetime.datetime(2024, 2, 19, 10, 23),
  datetime.timedelta(seconds=173)),
 ('123',
  '1001',
  datetime.datetime(2024, 2, 19, 9, 45),
  datetime.timedelta(seconds=557)),
 ('123',
  '1001',
  datetime.datetime(2024, 2, 19, 10, 5),
  datetime.timedelta(seconds=290)),
 ('169',
  '1001',
  datetime.dateti

In [20]:
columns = ["Bus line", "Bus stop", "Time", "Delay"]

df = pd.DataFrame(delayed_buses, columns=columns)

df

Bus line Bus stop                Time           Delay
0         147     1001 2024-02-19 10:27:00 0 days 00:04:07
1         166     1001 2024-02-19 09:54:00 0 days 00:04:26
2         509     1001 2024-02-19 10:03:00 0 days 00:02:39
3         138     1001 2024-02-19 09:44:00 0 days 00:05:12
4         166     1001 2024-02-19 10:04:00 0 days 00:04:48
...       ...      ...                 ...             ...
7901      185     7104 2024-02-19 10:21:00 0 days 00:11:56
7902      185     7106 2024-02-19 10:03:00 0 days 00:02:36
7903      108     7107 2024-02-19 10:24:00 0 days 00:07:07
7904      162     7107 2024-02-19 09:38:00 0 days 00:04:08
7905      162     7107 2024-02-19 10:08:00 0 days 00:02:56

[7906 rows x 4 columns]

In [21]:
df.sort_values(by="Delay")

Bus line Bus stop                Time           Delay
2211      509     2140 2024-02-19 10:21:00 0 days 00:02:00
1501      143     2015 2024-02-19 10:31:00 0 days 00:02:00
3934      179     3190 2024-02-19 10:16:00 0 days 00:02:00
7745      162     7072 2024-02-19 10:31:00 0 days 00:02:00
5157      191     4094 2024-02-19 09:38:00 0 days 00:02:00
...       ...      ...                 ...             ...
88        326     1014 2024-02-19 09:39:00 0 days 00:52:05
2573      722     2291 2024-02-19 09:40:00 0 days 00:53:01
2671      219     2371 2024-02-19 09:37:00 0 days 00:54:04
736       332     1173 2024-02-19 09:36:00 0 days 00:55:06
5363      721     4156 2024-02-19 09:36:00 0 days 00:55:07

[7906 rows x 4 columns]

In [22]:
df.groupby('Bus line').agg({'Delay': 'mean'}).reset_index().sort_values(by='Delay')

Bus line                     Delay
172      720           0 days 00:02:01
208      L31           0 days 00:02:12
194      L-2           0 days 00:02:23
164      711           0 days 00:02:25
132      349 0 days 00:02:38.777777777
..       ...                       ...
216      L46           0 days 00:30:00
179      729 0 days 00:30:42.333333333
193      L-1           0 days 00:31:59
174      722    0 days 00:50:33.500000
130      332           0 days 00:55:06

[225 rows x 2 columns]

In [23]:
df['Delay'].mean()

Timedelta('0 days 00:07:29.045914495')